In [ ]:
# ..... annotate CM cells ..... #

In [2]:
library(Seurat)
library(SingleCellExperiment)
library(MetaMarkers)
library(data.table)
library(dplyr)

In [3]:
# load list of orthologs
om = read.delim('mouse_turtle_orthologs_biomart.txt', sep = '\t')
colnames(om) <- c('mouse', 'turtle', 'LCA', 'homology_type', 'confidence')
om <- om[which(om[,1]!='' & om[,2]!='' & !is.na(om[,5]) & om[,5]==1 & om[,4]=='ortholog_one2one'),]
dim(om)
om[1,]

[1] 11125     5

mouse  turtle LCA        homology_type    confidence
11 mt-Nd2 ND2    Vertebrata ortholog_one2one 1

In [15]:
# load markers
markers = fread('~/septation/devCellPy_markers_res3.csv.gz')
markers$gene <- om$turtle[match(markers$gene, om$mouse)]
markers <- markers[!is.na(markers$gene),]
ctypes = unique(markers$cell_type)

# get top n markers for each cell type
markers$rank = NA
for(ii in 1:length(ctypes)){
    id = which(markers$cell_type==ctypes[ii])
    markers$rank[id] = 1:length(id)
}
markers[1:2,]

# tibble of group, cell_type, gene, rank
top_markers = as_tibble(markers[which(markers$rank<=200),c('group', 'cell_type', 'gene', 'rank', 'fold_change', 'auroc')])
top_markers[1:2,]

group cell_type gene   fold_change auroc     log_fdr   population_size
1 all   LV CM     CITED1 14.139443   0.9195970 -1454.237 1535           
2 all   LV CM     HAND1   4.105356   0.8644412 -1096.875 1535           
  population_fraction average_expression se_expression detection_rate
1 0.100821            1083.2376          27.824069     0.9472313     
2 0.100821             193.3223           3.822618     0.9022801     
  fold_change_detection precision recall    rank
1 2.406308              0.2127286 0.9472313 1   
2 4.074849              0.3143441 0.9022801 2

group cell_type gene   rank fold_change auroc    
1 all   LV CM     CITED1 1    14.139443   0.9195970
2 all   LV CM     HAND1  2     4.105356   0.8644412

In [6]:
# list of stages and samples
stages = rep(c('Stage_14', 'Stage_17', 'Stage_21'), each = 3)
samples = paste0('sample', c('4', '7', '8A', '3_Triangle', '5B', '5Y', '1A', '1B', '2'))

In [39]:
# load data
id = 9
currstage1 = stages[id]
currsmp1 = samples[id]
file0 = paste0(currstage1, '_', currsmp1, '_data.rds')
sc1 = readRDS(file0)

# load previous marker set (KS)
newdf2 = read.delim(paste0(currstage1, '_', currsmp1, '_Knight-Schrijver_celltypes.csv'), sep = ',')
sc1$class = newdf2$class[match(colnames(sc1), newdf2$barcode)]
sc1 <- sc1[,sc1$class %in% 'Cardiomyocytes']

# get SCE object
sc3 = SingleCellExperiment(list(counts = GetAssayData(sc1, 'counts')))
colData(sc3) <- DataFrame(sc1@meta.data)
assay(sc3, "cpm") = convert_to_cpm(assay(sc3))

In [40]:
# predict cell type neighborhood
ct_scores = score_cells(log1p(cpm(sc3)), top_markers)
ct_enrichment = compute_marker_enrichment(ct_scores)
ct_pred = assign_cells(ct_scores)

ct_pred[1:3,]
table(ct_pred$predicted)

group predicted score    enrichment
Stage_21_sample2_AAAGAACAGACGCCAA-1 all   Septal CM 1.867867 1.142043  
Stage_21_sample2_AAAGAACTCTCTATAC-1 all   Septal CM 2.644428 1.074950  
Stage_21_sample2_AAAGGATCACTGGATT-1 all   Septal CM 1.880189 1.028869


    LV CM     RV CM Septal CM 
      115        41       241 

In [41]:
# save
newdf = data.frame(barcode = rownames(ct_pred), celltype = ct_pred$predicted)
newdf[1,]
write.table(newdf, file = paste0(currstage1, '_', currsmp1, '_CM_subtypes.csv'),
            sep = ',', row.names = F, col.names = T, quote = F)

barcode                             celltype 
1 Stage_21_sample2_AAAGAACAGACGCCAA-1 Septal CM